In [ ]:
!pip install pydantic-ai

In [9]:
!pip install pydantic

In [2]:
import asyncio
from pydantic_ai import Agent
from pydantic_ai.models.openai import OpenAIChatModel
from pydantic_ai.providers.ollama import OllamaProvider

In [3]:
ollama_provider = OllamaProvider(
    base_url='http://localhost:11434/v1' 
)

In [4]:
llm = OpenAIChatModel(
    model_name='gpt-oss:latest', # lub np. 'llama3'
    provider=ollama_provider
)

In [5]:
agent = Agent(model=llm)

In [6]:
prompt = "Dlaczego tak lubimy Pythona i SQLa? :)"

In [ ]:
result = await agent.run(prompt)


In [8]:
print(result.output)

**Dlaczego tak lubimy Pythona i SQL?**  
Oto kilka kluczowych powodów, które sprawiają, że oba te języki zyskują szerokie uznanie w świecie programowania i bazy danych.

| Python | SQL |
|--------|-----|
| **Czytelna składnia** – „czytelny kod w angielskim” to prawdziwa wizja: wiersze zaczynają się od zera, a bloki tworzy wcięcia. Dzięki temu szybko zrozumiesz, co robi program. | **Deklaratywny charakter** – piszesz, co *chcesz* zrobić (np. „pokaż mi wszystkie rekordy”), a system decyduje, jak to wykonać. |
| **Wszechstronność** – od skryptów automatyzujących, przez web‑frameworki (Django, Flask), po naukę maszynową (NumPy, Pandas, scikit‑learn). | **Uniwersalność danych** – standard SQL jest używany w każdej relacyjnej bazie (PostgreSQL, MySQL, Oracle…) i często odtwarzany w innymi systemach (ex. BigQuery, Snowflake). |
| **Bogactwo bibliotek i ekosystemu** – setki pakietów dostępnych w PyPI. Nie musisz pisać wszystko od zera. | **Silne zarządzanie danymi** – transakcje, indeksy, cons

In [10]:
from pydantic import BaseModel, Field

In [13]:
sys_prompt = "Twoje zadanie to pobieranie danych o zadaniach do wykonania i zwracanie ich w przyjazdnej formie. Na podstawie treści zadania stwórz również haiku"

In [15]:
class TodoItem(BaseModel):
    userId: int
    id: int
    title: str = Field(description="Tytuł zadania do wykonania")
    completed: bool = Field(description="Czy zadanie zostało ukończone")
    haiku: str = Field(description="Krótkie haiku po polsku o treści zadania")

In [17]:
agent2 = Agent(
    model=llm,  
    output_type=TodoItem,  
    system_prompt=sys_prompt,
)

In [28]:
import requests
import json

In [19]:
@agent2.tool_plain
def get_todo_item(item_id: int) -> str:
    """
    Pobiera pojedyncze zadanie (to-do) z publicznego API JSONPlaceholder
    na podstawie jego ID. Zwraca dane jako string w formacie JSON.
    """
    print(f"--- WYWOŁANIE NARZĘDZIA: get_todo_item(item_id={item_id}) ---")
    try:
        response = requests.get(f"https://jsonplaceholder.typicode.com/todos/{item_id}")
        response.raise_for_status() # Sprawdź, czy nie ma błędu HTTP
        
        # Zwracamy tekst (string JSON), AI samo go zinterpretuje
        print(f"--- NARZĘDZIE ZWRÓCIŁO: {response.text} ---")
        return response.text 
    
    except requests.RequestException as e:
        print(f"--- BŁĄD NARZĘDZIA: {e} ---")
        return json.dumps({"error": str(e)})

In [20]:
user_question = "Pobierz mi pełne dane dla zadania o ID 7 i zwróć je jako obiekt."

In [24]:
result_object = await agent2.run(user_question)

--- WYWOŁANIE NARZĘDZIA: get_todo_item(item_id=7) ---
--- NARZĘDZIE ZWRÓCIŁO: {
  "userId": 1,
  "id": 7,
  "title": "illo expedita consequatur quia in",
  "completed": false
} ---


In [37]:
print(result_object.output.model_dump_json(indent=2))

{
  "userId": 1,
  "id": 7,
  "title": "illo expedita consequatur quia in",
  "completed": false,
  "haiku": "Brak zadań dziś\nŚwiatła w ciemności słabych\nCzas przyszłości"
}


In [40]:
class ChatContext(BaseModel):
    user_name: str
    conversation_id: str
    preferences: dict = Field(default_factory=dict)


agent = Agent(
    model=llm,
    deps_type=ChatContext,
    system_prompt="Jesteś pomocnym asystentem. Pamiętaj o kontekście rozmowy."
)

# Inicjalizacja
context = ChatContext(
    user_name="Anna",
    conversation_id="conv-456",
    preferences={"language": "pl", "style": "formal"}
)
history = []

# Pierwsza wymiana
result1 = await agent.run(
    "Potrzebuję pomocy z Pythonem",
    deps=context,
    message_history=history
)
history = result1.all_messages()

# Druga wymiana - agent wie o czym rozmawialiśmy
result2 = await agent.run(
    "A co z tym frameworkiem, o którym wspomniałeś?",
    deps=context,
    message_history=history
)
history = result2.all_messages()

In [41]:
print(history)

[ModelRequest(parts=[SystemPromptPart(content='Jesteś pomocnym asystentem. Pamiętaj o kontekście rozmowy.', timestamp=datetime.datetime(2025, 11, 7, 21, 33, 48, 659096, tzinfo=datetime.timezone.utc)), UserPromptPart(content='Potrzebuję pomocy z Pythonem', timestamp=datetime.datetime(2025, 11, 7, 21, 33, 48, 659102, tzinfo=datetime.timezone.utc))]), ModelResponse(parts=[ThinkingPart(content='User says "Potrzebuję pomocy z Pythonem" which means "I need help with Python". We need to ask clarifying question or ask what specific help they need. They haven\'t provided details. Since we\'re an assistant that can help. According to instructions: "Jesteś pomocnym asystentem. Pamiętaj o kontekście rozmowy." It\'s a generic. Should respond politely and ask what they specifically need. Probably ask: "Czego konkretnego potrzebujesz? Czy masz problem z jakimś kodem, błędnym wynikiem, czy chcesz porozmawiać o konkretnym zagadnieniu, np. POO, pandas, itd.?"', id='reasoning', provider_name='ollama'), T